DATA INGESTION

In [0]:
df=spark.read.text("dbfs:/FileStore/logfiles_compressed.txt")


DATA TRANSFORMATIONS

REDUCE NUMBER OF ROWS

In [0]:
from pyspark.sql.functions import monotonically_increasing_id
# Add an index column
df = df.withColumn("index", monotonically_increasing_id())
# Define the number of rows to remove
num_rows_to_remove = 90000 
# Remove the first 'num_rows_to_remove' rows
df = df.filter(df.index >= num_rows_to_remove)

In [0]:
df.show()

+--------------------+-----+
|               value|index|
+--------------------+-----+
|57.80.71.88 - - [...|90000|
|90.102.174.19 - -...|90001|
|185.77.173.108 - ...|90002|
|138.239.25.244 - ...|90003|
|142.137.233.25 - ...|90004|
|111.242.146.60 - ...|90005|
|83.215.160.190 - ...|90006|
|141.96.187.190 - ...|90007|
|236.188.158.231 -...|90008|
|162.5.177.23 - - ...|90009|
|130.107.192.62 - ...|90010|
|219.31.249.33 - -...|90011|
|215.15.30.31 - - ...|90012|
|182.28.115.146 - ...|90013|
|173.238.139.201 -...|90014|
|37.143.82.168 - -...|90015|
|14.41.116.160 - -...|90016|
|212.139.39.184 - ...|90017|
|99.1.87.96 - - [2...|90018|
|110.152.22.92 - -...|90019|
+--------------------+-----+
only showing top 20 rows



SPLIT DATA INTO COLUMNS USING REGULAR EXPRESSION

In [0]:
from pyspark.sql.functions import split, regexp_extract

log_pattern = r'(\d{1,3}\.\d{1,3}\.\d{1,3}\.\d{1,3}) - - \[(.*?)\] "(.*?) (.*?) (.*?)" (\d{3}) (\d+) "-" "(.*?)" (\d+)'
df = df.select(regexp_extract('value', log_pattern, 1).alias('ip_client'),
                     regexp_extract('value', log_pattern, 2).alias('date_time'),
                     regexp_extract('value', log_pattern, 3).alias('request_type'),
                     regexp_extract('value', log_pattern, 4).alias('API'),
                     regexp_extract('value', log_pattern, 5).alias('protocol_version'),
                     regexp_extract('value', log_pattern, 6).cast('integer').alias('status_code'),
                     regexp_extract('value', log_pattern, 7).cast('integer').alias('byte'),
                     regexp_extract('value', log_pattern, 8).alias('Referrer'),
                     regexp_extract('value', log_pattern, 9).cast('integer').alias('response_time'))
 

In [0]:
df.show()

+--------------+--------------------+------------+--------------------+----------------+-----------+----+--------------------+-------------+
|     ip_client|           date_time|request_type|                 API|protocol_version|status_code|byte|            Referrer|response_time|
+--------------+--------------------+------------+--------------------+----------------+-----------+----+--------------------+-------------+
|   57.80.71.88|27/Dec/2037:12:00...|        POST|          /usr/admin|        HTTP/1.0|        303|4927|Mozilla/5.0 (Linu...|         4795|
|              |                    |            |                    |                |       null|null|                    |         null|
|185.77.173.108|27/Dec/2037:12:00...|        POST|          /usr/admin|        HTTP/1.0|        500|5082|Mozilla/5.0 (iPho...|          831|
|138.239.25.244|27/Dec/2037:12:00...|         GET|          /usr/admin|        HTTP/1.0|        403|4953|Mozilla/5.0 (Maci...|         2485|
|142.137.233.

DROP NULL VALUES FROM ALL COLUMNS

In [0]:
df=df.na.drop(subset=["status_code","byte","response_time"])

EXTRACT DATE FROM DATE_TIME

In [0]:
from pyspark.sql.functions import to_date
df = df.withColumn('date', to_date("date_time", 'dd/MMM/yyyy:HH:mm:ss Z'))

In [0]:
df.printSchema()

root
 |-- ip_client: string (nullable = true)
 |-- date_time: string (nullable = true)
 |-- request_type: string (nullable = true)
 |-- status_code: integer (nullable = true)
 |-- Referrer: string (nullable = true)
 |-- response_time: integer (nullable = true)
 |-- date: date (nullable = true)



DROP UNWANTED COLUMNS

In [0]:
df=df.drop("byte","API","protocol_version")
display(df)


ip_client date_time request_type status_code Referrer response_time date 57.80.71.88 27/Dec/2037:12:00:00 +0530 POST 303 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 4795 2037-12-27 185.77.173.108 27/Dec/2037:12:00:00 +0530 POST 500 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 831 2037-12-27 138.239.25.244 27/Dec/2037:12:00:00 +0530 GET 403 Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 2485 2037-12-27 142.137.233.25 27/Dec/2037:12:00:00 +0530 POST 304 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 1002 2037-12-27 111.242.146.60 27/Dec/2037:12:00:00 +0530 POST 304 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 4247 2037-12-27 141.96.187.190 27/Dec/2037:12:00:00 +0530 GET 304 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 1948 2037-12-27 162.5.177.23 27/Dec/2037:12:00:00 +0530 GET 500 Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 1834 2037-12-27 14.41.116.160 27/Dec/2037:12:00:00 +0530 POST 200 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 2005 2037-12-27 212.139.39.184 27/Dec/2037:12:00:00 +0530 GET 500 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 2605 2037-12-27 110.152.22.92 27/Dec/2037:12:00:00 +0530 PUT 304 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 2571 2037-12-27 150.81.66.207 27/Dec/2037:12:00:00 +0530 DELETE 403 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 284 2037-12-27 15.49.125.197 27/Dec/2037:12:00:00 +0530 PUT 303 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 88 2037-12-27 184.176.142.27 27/Dec/2037:12:00:00 +0530 POST 403 Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 4543 2037-12-27 114.77.58.182 27/Dec/2037:12:00:00 +0530 PUT 304 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 4457 2037-12-27 196.138.235.76 27/Dec/2037:12:00:00 +0530 DELETE 304 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 4789 2037-12-27 144.16.20.233 27/Dec/2037:12:00:00 +0530 GET 403 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 1176 2037-12-27 136.231.139.11 27/Dec/2037:12:00:00 +0530 GET 303 Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 4452 2037-12-27 67.25.123.195 27/Dec/2037:12:00:00 +0530 DELETE 200 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 3580 2037-12-27 15.9.160.205 27/Dec/2037:12:00:00 +0530 PUT 404 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 1025 2037-12-27 51.89.89.159 27/Dec/2037:12:00:00 +0530 GET 304 Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 3276 2037-12-27 214.33.40.57 27/Dec/2037:12:00:00 +0530 POST 303 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebK

DATA ANALYSIS

1. POPULAR PAGES ON THE BASIS OF REFERRER

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.window import *
popular_page=df.groupBy("referrer").count().orderBy('count', ascending=False)
display(popular_page)

referrer count Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 45641 Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 45614 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 45572 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 45525 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 45497 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 45485 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 45406 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 45383 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36 OPR/73.0.3856.329 45291 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 45273

Databricks visualization. Run in Databricks to view.

2. NUMBER OF UNIQUE HOSTS

In [0]:
unique_hosts=df.select("referrer").distinct()
display(unique_hosts)


referrer Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36 OPR/73.0.3856.329 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1

Databricks visualization. Run in Databricks to view.

UNIQUE HOSTS ON DAILY BASIS

In [0]:
unique_host_per_days=df.groupBy("date").agg(countDistinct("Referrer").alias("unique_visits"))
display(unique_host_per_days)

date unique_visits 2037-12-27 10

3. AVERAGE RESPONSE TIME FOR EACH REFERRER

In [0]:

avg_response_time=df.groupBy("referrer").avg("response_time")
display(avg_response_time)

referrer avg(response_time) Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 2495.183101679309 Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 2493.6920093775334 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 2499.9044991977494 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 2504.159553136637 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 2495.406311941153 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36 OPR/73.0.3856.329 2499.3663641783137 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 2510.2100164744647 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 2502.6264881938464 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 2497.820820050566 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 2509.7733476696217

Databricks visualization. Run in Databricks to view.

4. MAXIMUM RESPONSE TIME FOR EACH REFERRER

In [0]:
max_response_time=df.groupBy("referrer").max("response_time")
display(max_response_time)

referrer max(response_time) Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 5000 Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 5000 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 5000 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 5000 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 5000 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36 OPR/73.0.3856.329 5000 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 5000 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 5000 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 5000 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 5000

Databricks visualization. Run in Databricks to view.

5. RATE OF ERRORS ON EACH REFERRER

In [0]:
errors=df.filter(df.status_code!=200).groupBy("referrer").count()
display(errors)


referrer count Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_3) AppleWebKit/537.75.14 (KHTML, like Gecko) Version/7.0.3 Safari/7046A194A 39082 Mozilla/5.0 (Android 10; Mobile; rv:84.0) Gecko/84.0 Firefox/84.0 39125 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/77.0.3865.116 Mobile Safari/537.36 EdgA/45.12.4.5121 38993 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36 38949 Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:84.0) Gecko/20100101 Firefox/84.0 39010 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36 OPR/73.0.3856.329 38882 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.198 Mobile Safari/537.36 OPR/61.2.3076.56749 39043 Mozilla/5.0 (Linux; Android 10; ONEPLUS A6000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Mobile Safari/537.36 38731 Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4380.0 Safari/537.36 Edg/89.0.759.0 39027 Mozilla/5.0 (iPhone; CPU iPhone OS 12_4_9 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/12.1.2 Mobile/15E148 Safari/604.1 39078

Databricks visualization. Run in Databricks to view.